# Ion Implantation 

In [ ]:
# numpy for mathematical operations and pyvista for 3-D visualization
import numpy as np
import matplotlib 
from matplotlib import image
from numba import jit,prange
import matplotlib.pyplot as plt 
from mpl_toolkits.mplot3d import Axes3D
import platform
from PIL import Image
%matplotlib osx 

# Background
Ion Implanters work as small scale particle accelerators. Given that the chamber is within a vacuum, the accelerated ions are extremely unlikely to deflect. As a result the main parameters that determine the implantation behavior are the **acceleration energy** and **atomic mass** of the ions. For this simulation we will use Boron or Arsenic Ions and a common range of acceleration energies (between 10keV and 100keV). 

In [ ]:
# Dictionary of Ions and Masses(kg) 
iondict = {
    "boron" : 1.83e-26,
    "arsenic" : 4.5e-25 
}

In [ ]:
# Dictionary of common acceleration energies (keV) mapped to Joules 
acceldict = {
    "10keV": 1.602e-15,
    "20keV": 3.204e-15, 
    "30keV": 4.806e-15,
    "40keV": 6.408e-15,
    "50keV": 8.01e-15, 
    "60keV": 9.612e-15,
    "70keV": 1.1214e-14,
    "80keV": 1.2816e-14,
    "90keV": 1.4418e-14,
    "100keV": 1.602e-14
}

# Substrate Visual 
For this simulation we will make a uniform 1 $\mu m^3 $ cube to represent a section of implant material. 

In [ ]:
num_points = 201

x = np.linspace (0, 1, num_points)
y = np.linspace(0, 1, num_points)
z = np.linspace(0, 1, num_points)

X,Y,Z = np.meshgrid(x,y,z)
fig = plt.figure(figsize=(8, 6)) 
ax = fig.add_subplot(111,projection='3d') 
 
ax.scatter(X,Y,Z,color='gray',alpha=1.0)
plt.show()

# Modeling the implantation 
We will model the implantation as a Diffusion Limited Aggregation which represents the movement of ions as they collide off the base silicon. 

In [ ]:
# Calculate the velocity of based on the mass and energy 
molecule = input("Enter the implanted ion (either 'boron' or 'arsenic'): ") 
energy = input("Enter the implantation energy in keV:  ")
mass = iondict[molecule]
accel = acceldict[str(energy) + 'keV']
velocity = np.sqrt(2* accel / mass)
print("velocity: ",velocity, "m/s")

Since the movement of the atoms is dependent on the atomic size, number of collisions, and remaining energy. Thus we develop a variation of the DLA algorithm that varies the probability of moving "down" over time as more collisions occur. 
### Factors 
**Atom Size** - Given the size of the atoms, either the ions are more likely to collide with atomic nuclei or electrons. Boron is more succeptible to electron "stopping" and thus will have a slower change over time than Arsenic which will suffer from nuclear "stopping" which leads to a greater "slowing". 
**Velocity** - Velocity will limit the movement of the atoms over time. 

In [ ]:
# define an update function that changes the velocity and probabilities based upon each iteration and molecule type 
@jit
def update(v,velocity,pxp,pxn,pyp,pyn,pzp,pzn): 
    global molecule,energy
    
    # update velocity 
    reduction = 0
    if molecule == 'boron': 
    # boron is lighter so more time to iterate 
        reduction = velocity / (float(energy) *  1.028) # rough factor based on profiles from RC Jaeger textbook
    else: 
        #arsenic is heavier so slower 
        reduction = velocity / (float(energy) * 0.539)
    # The rough reduction factor of atomic collisions 
    vel_update = v - reduction 
    
    #update all the probabilities over time 
    pxp_update = pxp + 0.002 
    pxn_update = pxn + 0.002
    pyp_update = pyp + 0.002 
    pyn_update = pyn + 0.002 
    pzn_update = pzn - 0.01 
    pzp_update = pzp + 0.002
    
    #return the resulting array 
    res = np.array([vel_update,pxp_update,pxn_update, pyp_update, pyn_update, pzp_update, pzn_update])
    return res 
    
    

# DLA Code 

In [ ]:
# set up a relatively small amount of particles and model a 3-dimensional DLA problem 
nParticles = 100
# set of points to build a scatter graph 
points_x = [100]
points_y = [100] 
points_z = [200]
# Final point locations and velocities 
fpointx = []
fpointy = []
fpointz = []
fpointv = []

#boundary parameters 
maxX = num_points 
maxY = num_points  
maxZ = num_points 

# frames for GIF 
frames = []

In [ ]:
 def display(points_x, points_y, points_z):
    global X,Y,Z,frames, molecule, energy 

    fig = plt.figure(figsize=(21,7))
    fig.suptitle(("Model of Implantation of " +  molecule + " at " + str(energy) + " keV."))
    # our new points
    ax1 = fig.add_subplot(131, projection='3d')
    #ax1.axis('off')
    ax1.scatter(X,Y,Z,color='gray',alpha=0.002)
    ax1.scatter(X[points_x[:],points_x[:],points_x[:]], Y[points_y[:],points_y[:],points_y[:]], 
    Z[points_z[:],points_z[:],points_z[:]],color='blue')
    ax1.set_title("3-Dimensional View of Ion Paths")

    # plot the x-z and y-z dist 
    ax2 = fig.add_subplot(132)
    ax2.scatter(X[points_x[:],points_x[:],points_x[:]],Z[points_z[:],points_z[:],points_z[:]],color='blue')
    ax2.set_ylabel('Depth (Z) (um)')
    ax2.set_xlabel('X (um)') 
    ax2.set_xlim(0,1)
    ax2.set_ylim(0,1)
    ax2.set_title('X-Z') 

    ax3 = fig.add_subplot(133)
    ax3.scatter(Y[points_y[:],points_y[:],points_y[:]],Z[points_z[:],points_z[:],points_z[:]], color='blue')
    ax3.set
    ax3.set_ylabel('Depth (Z) (um)')
    ax3.set_xlabel('Y (um)') 
    ax3.set_title('Y-Z')
    ax3.set_xlim(0,1)
    ax3.set_ylim(0,1)
    # export pngs to create a gif
    i = len(frames)
    print("Exporting image...") 
    plt.savefig(f'frame_{i}.png', bbox_inches='tight')  # Save each frame as a PNG file
    #print("Exported") 
    frames.append(Image.open(f'frame_{i}.png'))
    plt.show()

In [ ]:
# Show the initial point as a test
display(points_x,points_y,points_z)

In [ ]:
# DLA Function to be optimized by numba 
@jit
def DLA(points_x,points_y,point_z):
    global fpointx, fpointy, fpointz,fpointv,maxX,maxY,maxZ 
    for i in range(0,nParticles):
        x = 100 
        y = 100
        z = 200
        print("particle #",i)
        v = velocity 
        pxp = 1e-10 
        pxn = 1e-10 
        pyp = 1e-10 
        pyn = 1e-10 
        pzp = 1e-10 
        pzn = 1.0 - pxp - pxn - pyp - pyn - pzp
        if( (i > 0) and (i % 10 == 0)): 
            display(points_x,points_y,points_z)
        while True: 
            xOrg = x
            yOrg = y
            zOrg = z 
            vOrg = v 

            # If the particles velocity is less than or equal to zero it has reached its final position
            if (vOrg <= 0):
                # append the final values 
                fpointx.append(x)
                fpointy.append(y)
                fpointz.append(z) 
                fpointv.append(v)
                break 

            r = np.random.random(); # Random float:  0.0 <= r < 1.0
            #based on the value of 'r', move the particle

            if r >= 0.0 and r < pxn: 
                # go in the negative x 
                x = xOrg - 1
            elif r >= pxp and r < pxp + pxn: 
                # go in positive x 
                x = xOrg + 1
            elif r >= pxp + pxn and r < pxp + pxn + pyp: 
                # go up 
                y = yOrg + 1 
            elif r >= pxp + pxn + pyp and r < pxp + pxn + pyp + pyn: 
                #go down 
                y = yOrg - 1
            elif r >= pxp + pxn + pyp + pyn and r < pxp + pxn + pyp + pyn + pzn: 
                # negative z 
                z = zOrg - 1 
            else: 
                z = zOrg + 1

            #boundary condition
            if x >= maxX: 
                x = maxX - 1 
            if x < 0: 
                x = 0 
            if y >= maxY: 
                y = maxY - 1 
            if y < 0: 
                 y = 0 
            if z < 0: 
                z = 0 
            # check if the point is already occupied 

            xp = x - 1 if (x > 0 and x < maxX - 1) else (0 if (x >= maxX - 1) else maxX - 1) 
            xm =  x + 1 if (x > 0 and x < maxX - 1) else (0 if (x >= maxX - 1) else maxX - 1)
            yp = y - 1 if (y > 0 and y < maxY - 1) else (0 if (y >= maxY - 1) else maxY - 1)
            ym = y + 1 if (y > 0 and y < maxY - 1) else (0 if (y >= maxY - 1) else maxY - 1)
            zp = z - 1
            zm = z + 1


            #perform the checks to see if the point is connected to another point 
            xpt = False 
            if xp in points_x: 
                xpt = True 
            xmt = False
            if xm in points_x: 
                xmt = True
            ypt = False 
            if ym in points_y: 
                ypt = True
            ymt = False 
            if ym in points_y: 
                xpt = True
            zpt = False 
            if zp in points_z: 
                zpt = True 
            zmt = False 
            if zm in points_z: 
                zpt = True 


                # plug in all the points in the vectors 
            if (not xpt or not xmt or not ypt or not ymt or not zpt or not zmt):
                points_x.append(x)
                points_y.append(y)
                points_z.append(z) 

                #print("Point: ",x,y,z, "in traveled.")
                #print("Velocity:",v)
            #update all the parameters 
            res = update(v,velocity,pxp,pxn,pyp,pyn,pzp,pzn)
            v = res[0]
            pxp = res[1]
            pxn = res[2]
            pyp = res[3]
            pyn = res[4]
            pzp = res[5]
            pzn = res[6]
    

In [ ]:
# Call the DLA function 
DLA(points_x,points_y,points_z)

#save the gif 
name = molecule + '_' + str(energy) + 'keV' + '.gif' 
frames[0].save(name, save_all=True, append_images=frames[1:], optimize=False, duration=1000, loop=0)


In [ ]:
# stack and export the final points 
data = np.vstack((fpointx,fpointy,fpointz))
fname = molecule + '_' + str(energy) + 'keV' + '.csv' 
np.savetxt(fname, data, delimiter=",")